In [1]:
import os, sys
sys.path.append('../')
from data_functions import degree2radians, mapping_map_to_sphere, process_df, get_XYZV, create_spherical_heatmap_vals, get_lines

In [2]:
import numpy as np
import pandas as pd

df = pd.read_csv("../data/GlobalLandTemperaturesByCity.csv")
df = df[df['AverageTemperature'].notna()]
df['Year'] = [dt.split('-')[0] for dt in df['dt']]
tdf = process_df(df, ['City'], 'Latitude', 'Longitude', date=df['Year'].max(), date_var='Year'  )
tdf.head()

Latitude  Longitude                City         X         Y         Z  \
0    -52.24     -70.95        Punta Arenas  0.199869 -0.578819 -0.790583   
1    -45.81     -68.08  Comodoro Rivadavia  0.260213 -0.646648 -0.717032   
2    -45.81     169.62             Dunedin -0.685633  0.125590 -0.717032   
3    -44.20     172.17        Christchurch -0.710227  0.097668 -0.697165   
4    -42.59     -65.45              Trelew  0.305888 -0.669661 -0.676747   

   AverageTemperature  AverageTemperatureUncertainty  
0            6.297625                       0.778875  
1           11.192875                       0.624250  
2            7.932875                       0.819875  
3           11.036125                       0.722375  
4           13.206750                       0.588125

In [3]:
xyzv = get_XYZV(tdf, 'AverageTemperature')
XX, YY, ZZ, WW = create_spherical_heatmap_vals(xyzv)

In [8]:
import cartopy.feature as cf
import plotly.graph_objects as go
from scipy.ndimage import gaussian_filter

fig = go.Figure(data=[go.Surface(x=XX, y=YY, z=ZZ, surfacecolor=gaussian_filter(WW, sigma=2, mode='nearest'), opacity=1)] )

for x,y,z in [get_lines(g) for g in [cf.COASTLINE.geometries, cf.BORDERS.geometries] ]:
    fig.add_trace(go.Scatter3d(x=x, y=y, z=z, showlegend=False, hoverinfo='skip', mode='lines', line = dict(color='black', width=4)))

#fig.add_trace(go.Scatter3d(x=xyzv[:,0], y=xyzv[:,1],z=xyzv[:,2], mode='markers'))


fig.update_scenes(xaxis_visible=False, yaxis_visible=False,zaxis_visible=False )
fig.show()
fig.write_html('../plots/world_surface_with_datasrcs.html')